# Subspace Digital Twin, Sweep Credit Supply

* Shawn Anderson, December 2023*

In this notebook, we explore a test sweep over three credit supply definitions. These are: supply_issued, supply_earned, and supply_earned_minus_burned.

## Part 1. Exploratory Analysis

In [1]:
import pandas as pd
import hvplot.pandas

Load simulation data.

In [2]:
df = pd.read_pickle('../data/simulations/sweep_credit_supply-2023-12-19_15-20-33.pkl.gz')

In [3]:
df

days_passed  delta_days  delta_blocks  circulating_supply  \
0                0         NaN           NaN                 NaN   
13               1         1.0       14400.0        1.440039e+06   
26               2         1.0       14400.0        2.878894e+06   
39               3         1.0       14400.0        4.318089e+06   
52               4         1.0       14400.0        5.757444e+06   
...            ...         ...           ...                 ...   
27289          697         1.0       14400.0        4.591752e+08   
27302          698         1.0       14400.0        4.590588e+08   
27315          699         1.0       14400.0        4.589432e+08   
27328          700         1.0       14400.0        4.588284e+08   
27341          701         1.0       14400.0        4.587143e+08   

        user_supply  issued_supply  sum_of_stocks  block_utilization  \
0               NaN            NaN            NaN                NaN   
13     1.440039e+06   1.681440e+09   3.000000e+09           0.000011   
26     2.878894e+06   1.682880e+09   3.000000e+09           0.000011   
39     4.318101e+06   1.684320e+09   3.000000e+09           0.000011   
52     5.757506e+06   1.685760e+09   3.000000e+09           0.000011   
...             ...            ...            ...                ...   
27289  1.472341e+09   2.661288e+09   3.000000e+09           0.000011   
27302  1.474487e+09   2.662632e+09   3.000000e+09           0.000011   
27315  1.476632e+09   2.663976e+09   3.000000e+09           0.000011   
27328  1.478776e+09   2.665319e+09   3.000000e+09           0.000011   
27341  1.480921e+09   2.666662e+09   3.000000e+09           0.000011   

       dsf_relative_disbursal_per_day  reward_issuance_balance  ...  \
0                                 0.0             1.320000e+09  ...   
13                                0.0             1.318560e+09  ...   
26                                0.0             1.317120e+09  ...   
39                                0.0             1.315680e+09  ...   
52                                0.0             1.314240e+09  ...   
...                               ...                      ...  ...   
27289                             0.0             3.162963e+08  ...   
27302                             0.0             3.148563e+08  ...   
27315                             0.0             3.134163e+08  ...   
27328                             0.0             3.119762e+08  ...   
27341                             0.0             3.105362e+08  ...   

        base_fee_function  priority_fee_function  \
0      function: <lambda>     function: <lambda>   
13     function: <lambda>     function: <lambda>   
26     function: <lambda>     function: <lambda>   
39     function: <lambda>     function: <lambda>   
52     function: <lambda>     function: <lambda>   
...                   ...                    ...   
27289  function: <lambda>     function: <lambda>   
27302  function: <lambda>     function: <lambda>   
27315  function: <lambda>     function: <lambda>   
27328  function: <lambda>     function: <lambda>   
27341  function: <lambda>     function: <lambda>   

       compute_weights_per_tx_function  compute_weight_per_bundle_function  \
0                   function: <lambda>                  function: <lambda>   
13                  function: <lambda>                  function: <lambda>   
26                  function: <lambda>                  function: <lambda>   
39                  function: <lambda>                  function: <lambda>   
52                  function: <lambda>                  function: <lambda>   
...                                ...                                 ...   
27289               function: <lambda>                  function: <lambda>   
27302               function: <lambda>                  function: <lambda>   
27315               function: <lambda>                  function: <lambda>   
27328               function: <lambda>                  function: <

See numeric columns.

In [4]:
df.select_dtypes(include=['number']).columns

Index(['days_passed', 'delta_days', 'delta_blocks', 'circulating_supply',
       'user_supply', 'issued_supply', 'sum_of_stocks', 'block_utilization',
       'dsf_relative_disbursal_per_day', 'reward_issuance_balance',
       'other_issuance_balance', 'operators_balance', 'nominators_balance',
       'holders_balance', 'farmers_balance', 'staking_pool_balance',
       'fund_balance', 'burnt_balance', 'nominator_pool_shares',
       'operator_pool_shares', 'block_reward', 'history_size', 'space_pledged',
       'allocated_tokens', 'buffer_size', 'average_base_fee',
       'average_priority_fee', 'average_compute_weight_per_tx',
       'average_transaction_size', 'transaction_count',
       'average_compute_weight_per_bundle', 'average_bundle_size',
       'bundle_count', 'compute_fee_volume', 'storage_fee_volume',
       'rewards_to_nominators', 'simulation', 'subset', 'run', 'timestep',
       'average_compute_weight_per_budle', 'timestep_in_days',
       'block_time_in_seconds', 'arch

In [5]:
df_normalized = df.set_index('days_passed').select_dtypes(include=['number']).bfill() / df.set_index('days_passed').select_dtypes(include=['number']).max()
df_normalized = df_normalized.fillna(0)
df_normalized['label'] = df.set_index('days_passed')['label']
df_normalized = df_normalized.drop(['run', 'timestep', 'simulation', 'subset', 'timestep_in_days', 'block_time_in_seconds'], axis=1)
df_normalized.hvplot(groupby='label', height=1000, width=1400, ylim=(0,1))

:DynamicMap   [label]
   :NdOverlay   [Variable]
      :Curve   [days_passed]   (value)

In [6]:
differing_columns = df_normalized.groupby('days_passed').nunique()
differing_columns

delta_days  delta_blocks  circulating_supply  user_supply  \
days_passed                                                              
0                     1             1                   1            1   
1                     1             1                   1            1   
2                     1             1                   2            2   
3                     1             1                   2            2   
4                     1             1                   2            2   
...                 ...           ...                 ...          ...   
697                   1             1                   3            3   
698                   1             1                   3            3   
699                   1             1                   3            3   
700                   1             1                   3            3   
701                   1             1                   3            3   

             issued_supply  sum_of_stocks  block_utilization  \
days_passed                                                    
0                        1              1                  1   
1                        1              1                  1   
2                        1              1                  1   
3                        2              1                  1   
4                        2              2                  1   
...                    ...            ...                ...   
697                      3              3                  1   
698                      3              3                  1   
699                      3              3                  1   
700                      3              3                  1   
701                      3              2                  1   

             dsf_relative_disbursal_per_day  reward_issuance_balance  \
days_passed                                                            
0                                         1                        1   
1                                         1                        1   
2                                         1                        1   
3                                         1                        2   
4                                         1                        2   
...                                     ...                      ...   
697                                       1                        3   
698                                       1                        3   
699                                       1                        3   
700                                       1                        3   
701                                       1                        3   

             other_issuance_balance  ...  min_bundle_size  \
days_passed                          ...                    
0                                 1  ...                1   
1                                 1  ...                1   
2                                 1  ...                1   
3                                 1  ...                1   
4                                 1  ...                1   
...                             ...  ...              ...   
697                               1  ...                1   
698                               1  ...                1   
699                               1  ...                1   
700                               1  ...                1   
701                               1  ...                1   

             reward_proposer_share  max_credit_supply  \
days_passed                                             
0                                1                  1   
1                                1                  1   
2                                1                  1   
3                                1                  1   
4                                1                  1   
...                            ...                ...   
697                           

In [7]:
differing_values = df_normalized.groupby('days_passed').nunique()
differing_columns = list(differing_values.columns[differing_values.gt(1).any()])
differing_columns = df_normalized[differing_columns]

In [8]:
differing_columns

circulating_supply  user_supply  issued_supply  sum_of_stocks  \
days_passed                                                                  
0                      0.002797     0.000972       0.630541            1.0   
1                      0.002797     0.000972       0.630541            1.0   
2                      0.005591     0.001944       0.631081            1.0   
3                      0.008386     0.002916       0.631621            1.0   
4                      0.011182     0.003888       0.632161            1.0   
...                         ...          ...            ...            ...   
697                    0.891767     0.994207       0.997985            1.0   
698                    0.891541     0.995655       0.998489            1.0   
699                    0.891316     0.997104       0.998993            1.0   
700                    0.891093     0.998552       0.999496            1.0   
701                    0.890872     1.000000       1.000000            1.0   

             reward_issuance_balance  operators_balance  nominators_balance  \
days_passed                                                                   
0                           1.000000           0.000000            0.000000   
1                           0.998909           0.000000            0.000000   
2                           0.997818           0.000013            0.000003   
3                           0.996727           0.000054            0.000012   
4                           0.995636           0.000135            0.000030   
...                              ...                ...                 ...   
697                         0.239618           0.719817            0.949838   
698                         0.238527           0.719640            0.949519   
699                         0.237437           0.719465            0.949202   
700                         0.236346           0.719292            0.948886   
701                         0.235255           0.719121            0.948571   

             holders_balance  farmers_balance  staking_pool_balance  \
days_passed                                                           
0                   0.000000         0.000000          0.000000e+00   
1                   0.000212         0.049997          0.000000e+00   
2                   0.000588         0.097864          0.000000e+00   
3                   0.001160         0.143214          1.177056e-08   
4                   0.001909         0.186234          6.069463e-08   
...                      ...              ...                   ...   
697                 0.574979         0.999957          9.911562e-01   
698                 0.574861         0.999957          9.933686e-01   
699                 0.574744         0.999957          9.955800e-01   
700                 0.574628         0.999957          9.977905e-01   
701                 0.574514         0.999957          1.000000e+00   

             fund_balance  burnt_balance  nominator_pool_shares  \
days_passed                                                       
0                0.000000   0.000000e+00           0.000000e+00   
1                0.000000   0.000000e+00           0.000000e+00   
2                0.074425   0.000000e+00           0.000000e+00   
3                0.124098   0.000000e+00           6.905016e-09   
4                0.161389   5.012958e-11           3.577716e-08   
...                   ...            ...                    ...   
697              0.107105   9.830586e-01           9.906778e-01   
698              0.107289   9.872798e-01           9.930095e-01   
699              0.107473   9.915104e-01           9.953405e-01   
700              0.107657   9.957505e-01           9.976706e-01   
701              0.107841   1.000000e+00           1.000000e+00   

             operator_pool_shares  block_reward  storage_fee_volume  \
days_passed                                                           
0                    0.000000e+0

In [9]:
long_df = differing_columns.reset_index().melt(id_vars=['days_passed', 'label'], var_name='State', value_name='Value')
long_df

days_passed                       label               State     Value
0                0               supply-issued  circulating_supply  0.002797
1                1               supply-issued  circulating_supply  0.002797
2                2               supply-issued  circulating_supply  0.005591
3                3               supply-issued  circulating_supply  0.008386
4                4               supply-issued  circulating_supply  0.011182
...            ...                         ...                 ...       ...
33691          697  supply-earned-minus-burned  storage_fee_volume  0.002473
33692          698  supply-earned-minus-burned  storage_fee_volume  0.002473
33693          699  supply-earned-minus-burned  storage_fee_volume  0.002473
33694          700  supply-earned-minus-burned  storage_fee_volume  0.002473
33695          701  supply-earned-minus-burned  storage_fee_volume  0.002473

[33696 rows x 4 columns]

In [10]:
long_df.hvplot.line(
    x='days_passed', 
    y='Value', 
    by='label', 
    groupby='State',
)

:DynamicMap   [State]
   :NdOverlay   [label]
      :Curve   [days_passed]   (Value)

In [11]:
long_df[long_df['State'].isin(['fund_balance', 'storage_fee_volume', 'block_reward'])].hvplot(x='days_passed', y='Value', groupby='State', by='label')

:DynamicMap   [State]
   :NdOverlay   [label]
      :Curve   [days_passed]   (Value)

In [12]:
long_df[long_df['State'].isin(['fund_balance', 'storage_fee_volume', 'block_reward'])].hvplot(x='days_passed', y='Value', row='State', col='label', subplots=True, shared_axes=False)

:GridSpace   [State,label]
   :Curve   [days_passed]   (Value)

In [13]:
long_df.hvplot.line(x='days_passed', y='Value', by='State', groupby='label')

:DynamicMap   [label]
   :NdOverlay   [State]
      :Curve   [days_passed]   (Value)

In [14]:
long_df.hvplot.line(x='days_passed', y='Value', row='State', by='label', shared_axes=False)

:GridSpace   [State]
   :NdOverlay   [label]
      :Curve   [days_passed]   (Value)

In [29]:
y = ['circulating_supply', 'user_supply', 'issued_supply', 'staking_pool_balance', 'fund_balance', 'burnt_balance', 'reward_issuance_balance', 'farmers_balance', 'holders_balance', 'storage_fee_volume', 'space_pledged', 'history_size', 'replication_factor']

In [32]:
long_df[long_df['State'].isin(y)]

days_passed                       label               State     Value
0                0               supply-issued  circulating_supply  0.002797
1                1               supply-issued  circulating_supply  0.002797
2                2               supply-issued  circulating_supply  0.005591
3                3               supply-issued  circulating_supply  0.008386
4                4               supply-issued  circulating_supply  0.011182
...            ...                         ...                 ...       ...
33691          697  supply-earned-minus-burned  storage_fee_volume  0.002473
33692          698  supply-earned-minus-burned  storage_fee_volume  0.002473
33693          699  supply-earned-minus-burned  storage_fee_volume  0.002473
33694          700  supply-earned-minus-burned  storage_fee_volume  0.002473
33695          701  supply-earned-minus-burned  storage_fee_volume  0.002473

[21060 rows x 4 columns]

In [61]:
long_df[long_df['State'].isin(y)].hvplot(x='days_passed', y='Value', row='State', col='label', subplots=True, shared_axes=False, xaxis=False, yaxis=False)

:GridSpace   [State,label]
   :Curve   [days_passed]   (Value)